In [ ]:
!pip install sentence_transformers openai unstructured
!pip install plotly
!pip install langchain
!pip install tiktoken
!pip install matplotlib
%pip install -Uqqq rich openai tiktoken wandb langchain unstructured tabulate pdf2image chromadb gradio faiss-gpu


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 163.3/163.3 kB 4.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 267.1/267.1 kB 9.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.9/1.9 MB 14.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.6/75.6 kB 8.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 433.8/433.8 kB 16.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 274.7/274.7 kB 15.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 981.5/981.5 kB 18.6 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.4/3.4 MB 30.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 77.9/77.9 kB 9.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 23.7/23.7 MB 32.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 823.6/823.6 kB 51.0 M

In [ ]:
!pip install linkify-it-py

In [ ]:
import numpy as np
import os, random
from pathlib import Path
import tiktoken
from getpass import getpass
from rich.markdown import Markdown
from langchain.chains.qa_with_sources import load_qa_with_sources_chain

In [45]:
import torch
import sys
import csv

csv.field_size_limit(sys.maxsize)

# torch.has_mps

9223372036854775807

In [ ]:
# os.environ["OPENAI_API_KEY"] = getpass("")
#os.environ["OPENAI_API_KEY"] = “206143cbdb8d41ec94c654dec0eed59f”

In [ ]:

if os.getenv("OPENAI_API_KEY") is None:
  if any(['VSCODE' in x for x in os.environ.keys()]):
    print('Please enter password in the VS Code prompt at the top of your VS Code window!')
  os.environ["OPENAI_API_KEY"] = getpass("")

assert os.getenv("OPENAI_API_KEY", "").startswith("sk-"), "This doesn't look like a valid OpenAI API key"
print("OpenAI API key configured")

OpenAI API key configured


#Chunking and RAG

In [ ]:
from langchain.embeddings.openai import OpenAIEmbeddings
from langchain.text_splitter import CharacterTextSplitter
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.vectorstores import Chroma
from langchain.document_loaders import TextLoader
from langchain.chat_models import ChatOpenAI
from langchain import PromptTemplate
from langchain.chains import LLMChain
from langchain.chains.qa_with_sources import load_qa_with_sources_chain
from langchain.llms import OpenAI
from langchain.vectorstores import FAISS

In [ ]:
MODEL_NAME = "text-embedding-3-small"
# MODEL_NAME = "gpt-4"

In [ ]:
# from langchain.document_loaders import DirectoryLoader

# def find_md_files(directory):
#     "Find all markdown files in a directory and return a LangChain Document"
#     dl = DirectoryLoader(directory, "**/*.txt")
#     return dl.load()

# documents = find_md_files('data')
# len(documents)

In [ ]:
# documents

#upload files

In [ ]:
import pandas as pd

In [ ]:
from langchain.document_loaders.csv_loader import CSVLoader
# from langchain.docstore.document import Document
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.document_loaders import DirectoryLoader

In [ ]:
url='https://drive.google.com/file/d/1r2lol3qUPSu9l6cb2qbRTlw9IZM9O-C_/view?usp=sharing'
url='https://drive.google.com/uc?id=' + url.split('/')[-2]
df = pd.read_csv(url)


In [ ]:
df.head()

question  \
0                What is (are) Glaucoma ?   
1                  What causes Glaucoma ?   
2     What are the symptoms of Glaucoma ?   
3  What are the treatments for Glaucoma ?   
4                What is (are) Glaucoma ?   

                                              answer           source  \
0  Glaucoma is a group of diseases that can damag...  NIHSeniorHealth   
1  Nearly 2.7 million people have glaucoma, a lea...  NIHSeniorHealth   
2  Symptoms of Glaucoma  Glaucoma can develop in ...  NIHSeniorHealth   
3  Although open-angle glaucoma cannot be cured, ...  NIHSeniorHealth   
4  Glaucoma is a group of diseases that can damag...  NIHSeniorHealth   

  focus_area  
0   Glaucoma  
1   Glaucoma  
2   Glaucoma  
3   Glaucoma  
4   Glaucoma

In [ ]:
df.shape

(16412, 4)

In [ ]:
!mkdir data

In [ ]:
df[:100].to_csv('data/df_embed.csv',index=False)

1. Step 1: Read the data

In [ ]:
df.answer	[1]

'Nearly 2.7 million people have glaucoma, a leading cause of blindness in the United States. Although anyone can get glaucoma, some people are at higher risk. They include - African-Americans over age 40  - everyone over age 60, especially Hispanics/Latinos  - people with a family history of glaucoma. African-Americans over age 40 everyone over age 60, especially Hispanics/Latinos people with a family history of glaucoma.  In addition to age, eye pressure is a risk factor. Whether you develop glaucoma depends on the level of pressure your optic nerve can tolerate without being damaged. This level is different for each person. Thats why a comprehensive dilated eye exam is very important. It can help your eye care professional determine what level of eye pressure is normal for you. Another risk factor for optic nerve damage relates to blood pressure. Thus, it is important to also make sure that your blood pressure is at a proper level for your body by working with your medical doctor. (W

In [ ]:
df.head()

question  \
0                What is (are) Glaucoma ?   
1                  What causes Glaucoma ?   
2     What are the symptoms of Glaucoma ?   
3  What are the treatments for Glaucoma ?   
4                What is (are) Glaucoma ?   

                                              answer           source  \
0  Glaucoma is a group of diseases that can damag...  NIHSeniorHealth   
1  Nearly 2.7 million people have glaucoma, a lea...  NIHSeniorHealth   
2  Symptoms of Glaucoma  Glaucoma can develop in ...  NIHSeniorHealth   
3  Although open-angle glaucoma cannot be cured, ...  NIHSeniorHealth   
4  Glaucoma is a group of diseases that can damag...  NIHSeniorHealth   

  focus_area  
0   Glaucoma  
1   Glaucoma  
2   Glaucoma  
3   Glaucoma  
4   Glaucoma

In [ ]:
path= 'data/df_embed.csv'
loader = CSVLoader(file_path=path,source_column="answer")

data = loader.load()

In [ ]:
print(data[0])

page_content="question: What is (are) Glaucoma ?\nanswer: Glaucoma is a group of diseases that can damage the eye's optic nerve and result in vision loss and blindness. While glaucoma can strike anyone, the risk is much greater for people over 60. How Glaucoma Develops  There are several different types of glaucoma. Most of these involve the drainage system within the eye. At the front of the eye there is a small space called the anterior chamber. A clear fluid flows through this chamber and bathes and nourishes the nearby tissues. (Watch the video to learn more about glaucoma. To enlarge the video, click the brackets in the lower right-hand corner. To reduce the video, press the Escape (Esc) button on your keyboard.) In glaucoma, for still unknown reasons, the fluid drains too slowly out of the eye. As the fluid builds up, the pressure inside the eye rises. Unless this pressure is controlled, it may cause damage to the optic nerve and other parts of the eye and result in loss of visio

In [ ]:
print (f'You have {len(data)} document(s) in your data')
print (f'There are {len(data[0].page_content)} words in your document')

You have 100 document(s) in your data
There are 1938 words in your document


2. Breakdown data - Chunking Process

In [ ]:
text_splitter = RecursiveCharacterTextSplitter(chunk_size=1000, chunk_overlap=100)
texts = text_splitter.split_documents(data)

In [ ]:
len(texts)

329

In [ ]:
print (f'You now have {len(texts)} document(s) in your data')
print (f'There are {len(texts[1].page_content)} characters in your document')

You now have 329 document(s) in your data
There are 996 characters in your document


In [ ]:
texts[10]

Document(page_content='measures your side or peripheral vision. It helps your eye care professional tell if you have lost side vision, a sign of glaucoma. In a dilated eye exam, drops are placed in your eyes to widen, or dilate, the pupils. Your eye care professional uses a special magnifying lens to examine your retina and optic nerve for signs of damage and other eye problems. After the exam, your close-up vision may remain blurred for several hours. In tonometry, an instrument measures the pressure inside the eye. Numbing drops may be applied to your eye for this test. With pachymetry,  a numbing drop is applied to your eye. Your eye care professional uses an ultrasonic wave instrument to measure the thickness of your cornea.', metadata={'source': 'Symptoms of Glaucoma  Glaucoma can develop in one or both eyes. The most common type of glaucoma, open-angle glaucoma, has no symptoms at first. It causes no pain, and vision seems normal. Without treatment, people with glaucoma will slow

In [ ]:
!pip install -U langchain-openai
from langchain_openai import OpenAIEmbeddings
from langchain_openai import ChatOpenAI

In [ ]:
embeddings = OpenAIEmbeddings()
db = FAISS.from_documents(texts, embeddings)

In [ ]:
db.save_local("faiss_index")


In [ ]:
db_loaded = FAISS.load_local("faiss_index", embeddings,allow_dangerous_deserialization=True)

In [ ]:
query = """What are the causes of glaucoma"""

In [ ]:
def get_response_from_query(db, query, k=10):
    """

    """

    docs = db.similarity_search(query, k=k) # extremely important

    docs_page_content = " ".join([d.page_content for d in docs])

    # llm = BardLLM()
    llm = ChatOpenAI(model_name="gpt-3.5-turbo-16k",temperature=0)

    prompt = PromptTemplate(
        input_variables=["question", "docs"],
        template="""
        You are a bot that is open to discussions about different cultural, philosophical and political exchanges. I will use do different analysis to the articles provided to me. Stay truthful and if you weren't provided any resources give your oppinion only.
        Answer the following question: {question}
        By searching the following articles: {docs}

        Only use the factual information from the documents. Make sure to mention key phrases from the articles.

        If you feel like you don't have enough information to answer the question, say "I don't know".

        """,
    )

    chain = LLMChain(llm=llm, prompt=prompt)
    # chain = RetrievalQAWithSourcesChain.from_chain_type(llm=llm, prompt=prompt,
    #                                                     chain_type="stuff", retriever=db.as_retriever(), return_source_documents=True)

    response = chain.run(question=query, docs=docs_page_content,return_source_documents=True)
    r_text = str(response)

    ##evaluation part

    prompt_eval = PromptTemplate(
        input_variables=["answer", "docs"],
        template="""
        You job is to evaluate if the response to a given context is faithful.

        for the following: {answer}
        By searching the following article: {docs}

       Give a reason why they are similar or not, start with a Yes or a No.

        """,
    )

    chain_part_2 = LLMChain(llm=llm, prompt=prompt_eval)

    evals = chain_part_2.run(answer=r_text, docs=docs_page_content)


    return response,docs,evals

In [ ]:
answer,sources,evals=get_response_from_query(db_loaded,query,15)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The function `run` was deprecated in LangChain 0.1.0 and will be removed in 0.2.0. Use invoke instead.
  warn_deprecated(


In [ ]:
sources

[Document(page_content='question: What causes Glaucoma ?', metadata={'source': 'Nearly 2.7 million people have glaucoma, a leading cause of blindness in the United States. Although anyone can get glaucoma, some people are at higher risk. They include - African-Americans over age 40  - everyone over age 60, especially Hispanics/Latinos  - people with a family history of glaucoma. African-Americans over age 40 everyone over age 60, especially Hispanics/Latinos people with a family history of glaucoma.  In addition to age, eye pressure is a risk factor. Whether you develop glaucoma depends on the level of pressure your optic nerve can tolerate without being damaged. This level is different for each person. Thats why a comprehensive dilated eye exam is very important. It can help your eye care professional determine what level of eye pressure is normal for you. Another risk factor for optic nerve damage relates to blood pressure. Thus, it is important to also make sure that your blood pres

In [ ]:
from pprint import pprint

# Print question, answer, and evaluations
print("\n\n> Question:")
pprint(query)
print("\n> Answer:")
pprint(answer)
print("\n> Eval:")
pprint(evals)

# Print the relevant sources used for the answer
print("----------------------------------SOURCE DOCUMENTS---------------------------")
for document in sources:
    print("\n> " + document.metadata["source"])
    pprint(document.page_content[:1000])
print("----------------------------------SOURCE DOCUMENTS---------------------------")




> Question:
'What are the causes of glaucoma'

> Answer:
("Glaucoma is a group of diseases that can damage the eye's optic nerve and "
 'result in vision loss and blindness. The most common form of glaucoma is '
 'open-angle glaucoma, where the clear fluid in the eye drains too slowly, '
 'causing pressure to build up and potentially damage the optic nerve. The '
 'risk of glaucoma is higher for people over 60, African-Americans over age '
 '40, Hispanics/Latinos over age 60, and those with a family history of '
 'glaucoma. Glaucoma typically has no symptoms at first, but without '
 'treatment, it can lead to the loss of peripheral vision and eventually '
 'complete vision loss. While there is no cure for glaucoma, early diagnosis '
 'and treatment can help protect remaining vision. Treatment options include '
 'medication, laser surgery, and ongoing research to improve detection, '
 'treatment, and prevention of glaucoma.')

> Eval:
('No, the response is not faithful. The response d

In [46]:
import gradio as gr

In [47]:
def get_response_from_query(db, query, k=3):


    docs = db.similarity_search(query, k=k)

    docs_page_content = " ".join([d.page_content for d in docs])

    # llm = BardLLM()
    llm = ChatOpenAI(model_name="gpt-3.5-turbo-16k",temperature=0)

    prompt = PromptTemplate(
        input_variables=["question", "docs"],
        template="""
        A bot that is open to discussions about different cultural, philosophical and political exchanges. I will use do different analysis to the articles provided to me. Stay truthful and if you weren't provided any resources give your oppinion only.
        Answer the following question: {question}
        By searching the following articles: {docs}

        Only use the factual information from the documents. Make sure to mention key phrases from the articles.

        If you feel like you don't have enough information to answer the question, say "I don't know".

        """,
    )

    chain = LLMChain(llm=llm, prompt=prompt)
    # chain = RetrievalQAWithSourcesChain.from_chain_type(llm=llm, prompt=prompt,
    #                                                     chain_type="stuff", retriever=db.as_retriever(), return_source_documents=True)

    response = chain.run(question=query, docs=docs_page_content,return_source_documents=True)
    r_text = str(response)

    ##evaluation part

    prompt_eval = PromptTemplate(
        input_variables=["answer", "docs"],
        template="""
       You job is to evaluate if the response to a given context is faithful.

        for the following: {answer}
        By searching the following article: {docs}

       Give a reason why they are similar or not, start with a Yes or a No.
        """,
    )

    chain_part_2 = LLMChain(llm=llm, prompt=prompt_eval)


    evals = chain_part_2.run(answer=r_text, docs=docs_page_content)

    return response,docs,evals

In [48]:
from linkify_it import LinkifyIt

In [ ]:
#!pip list

In [49]:
def greet(query):

    answer,sources,evals = get_response_from_query(db,query,2)
    return answer,sources,evals
examples = [
    ["How to be happy"],
    ["Climate Change Challenges in Europe"],
    ["Philosophy in the world of Minimalism"],
    ["Hate Speech  vs Freedom of Speech"],
    ["Articles by Noam Chomsky on US Politics"],
    ["The importance of values and reflection"]
    ]
demo = gr.Interface(fn=greet, title="cicero-semantic-search", inputs="text",
                    outputs=[gr.components.Textbox(lines=3, label="Response"),
                             gr.components.Textbox(lines=3, label="Source"),
                             gr.components.Textbox(lines=3, label="Evaluation")],
                   examples=examples)

demo.launch(share=True)




Colab notebook detected. To show errors in colab notebook, set debug=True in launch()
Running on public URL: https://eeb7673436613da26c.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from Terminal to deploy to Spaces (https://huggingface.co/spaces)


In [ ]:
from gradio_client import Client

client = Client("https://baabf3218b5a239f65.gradio.live")
result = client.predict(
		"How to diagnose Paget's Disease of Bone ?",	# str  in 'query' Textbox component
		api_name="/predict"
)
print(result)

KeyboardInterrupt: 